# Team 4_4 Join from Raw datasets

## Join Description

## Dataset Feature Guide

Below is a concise field guide for your final dataset. For each feature we list: **Type**, **Source**, **When available**, **Leakage?**, and **Description / usage notes**.

---

### Keys & Provenance (do not drop)
| Feature | Type | Source | When available | Leakage? | Description / usage notes |
|---|---|---|---|---|---|
| `flight_id` | string | Derived | Always | No | Stable key: `FL_DATE|OP_UNIQUE_CARRIER|OP_CARRIER_FL_NUM|ORIGIN|DEST`. Use for joins/auditing. |
| `prediction_utc` | timestamp (UTC) | Derived | **T–2h** | No | Decision time in UTC used to pick “as-of” weather. Built from local schedule + airport timezone. |
| `origin_obs_utc` | timestamp (UTC) | Weather | **T–2h** | No | Timestamp of the weather observation actually used for origin (≤ `prediction_utc`). |
| `asof_minutes` | int | Derived | **T–2h** | No | Freshness of weather in minutes: `prediction_utc − origin_obs_utc` (0 = same hour; larger = older). |
| `origin_station_id` | string | Weather | **T–2h** | No | NOAA station chosen for origin (nearest then latest within 6h lookback). |
| `dest_station_id` | string | Weather | Pre-computed | No | Rank-1 nearest station to destination (location helpers only; no dest weather attached). |

---

### Flight & Schedule (model inputs)
| Feature | Type | Source | When available | Leakage? | Description / usage notes |
|---|---|---|---|---|---|
| `FL_DATE` | date | Flights | Always | No | Flight local calendar date. Combine with CRS times for timestamps. |
| `YEAR` / `QUARTER` / `MONTH` / `DAY_OF_MONTH` / `DAY_OF_WEEK` | int | Flights | Always | No | Calendar fields for seasonality/day-of-week effects. |
| `OP_UNIQUE_CARRIER` | string | Flights | Always | No | Carrier code (e.g., AA, DL). Categorical; encode appropriately. |
| `OP_CARRIER` | string | Flights | Always | No | Often duplicative of `OP_UNIQUE_CARRIER`; keep one to avoid redundancy. |
| `OP_CARRIER_FL_NUM` | int | Flights | Always | No | Flight number. High-cardinality; consider hashing or drop if not needed. |
| `TAIL_NUM` | string | Flights | Often | No | Aircraft tail (optional; sparse/reused). Use with care to avoid overfitting. |
| `CRS_DEP_TIME` | int (HHMM) | Flights | Always | No | Scheduled departure local time (e.g., 755 ⇒ 07:55). Derive hour buckets if useful. |
| `CRS_ARR_TIME` | int (HHMM) | Flights | Always | No | Scheduled arrival local time. |
| `CRS_ELAPSED_TIME` | int (min) | Flights | Always | No | Planned duration in minutes; helps normalize route length. |
| `ORIGIN` / `DEST` | string (IATA) | Flights | Always | No | Three-letter airport codes. Join keys to airport dim and station bridge. |
| `ORIGIN_AIRPORT_ID` / `DEST_AIRPORT_ID` | int | Flights | Always | No | Numeric airport identifiers (BTS). |
| `ORIGIN_CITY_NAME` / `DEST_CITY_NAME` | string | Flights | Always | No | Human-readable city names (may be redundant). |
| `ORIGIN_STATE_ABR` / `DEST_STATE_ABR` | string | Flights | Always | No | Two-letter state codes. |
| `DISTANCE` | double (miles) | Flights | Always | No | Great-circle distance; often inversely related to dep-delay rate. |
| `DISTANCE_GROUP` | int | Flights | Always | No | Distance bucket (BTS bins). Categorical alternative to continuous miles. |

---

### Origin Weather (as-of T–2h; model inputs)
> NOAA ISD fields often arrive as strings with units/qualifiers; parse to numeric and handle missing (“M”) as needed.

| Feature | Type | Source | When available | Leakage? | Description / usage notes |
|---|---|---|---|---|---|
| `HourlyDryBulbTemperature` | string → numeric | Weather | T–2h | No | Ambient air temperature. Parse numeric; watch units/qualifiers. |
| `HourlyDewPointTemperature` | string → numeric | Weather | T–2h | No | Dew point; with RH helps assess fog/icing risk. |
| `HourlyWetBulbTemperature` | string → numeric | Weather | T–2h | No | Wet-bulb temp; proxy for heat/humidity effects. |
| `HourlyPrecipitation` | string → numeric (in) | Weather | T–2h | No | Hourly precip. Many zeros; spikes predictive. |
| `HourlyWindSpeed` | string → numeric | Weather | T–2h | No | Sustained wind speed. Consider last-6h max as extra feature. |
| `HourlyWindDirection` | string → numeric (deg) | Weather | T–2h | No | 0–360°; consider sin/cos transform for cyclicity. |
| `HourlyWindGustSpeed` | string → numeric | Weather | T–2h | No | Gusts; sparse but predictive when present. |
| `HourlyVisibility` | string → numeric (mi) | Weather | T–2h | No | Surface visibility; lower ⇒ more delay risk. |
| `HourlyRelativeHumidity` | string → numeric (%) | Weather | T–2h | No | High RH + low visibility often impactful. |
| `HourlyStationPressure` | string → numeric (mb) | Weather | T–2h | No | Station pressure; consider deltas if available. |
| `HourlySeaLevelPressure` | string → numeric (mb) | Weather | T–2h | No | SLP; quality varies by station. |
| `HourlyAltimeterSetting` | string → numeric (inHg) | Weather | T–2h | No | Altimeter setting. |
| `HourlySkyConditions` | string (coded) | Weather | T–2h | No | Tokenize layers (FEW/BKN/OVC + heights). Multi-hot categorical works well. |
| `HourlyPresentWeatherType` | string (coded) | Weather | T–2h | No | Phenomena codes (RA, SN, FG, TS…). Parse into flags per phenomenon. |

---

### Location Helpers (model inputs; not labels)
| Feature | Type | Source | When available | Leakage? | Description / usage notes |
|---|---|---|---|---|---|
| `origin_station_lat` / `origin_station_lon` | double | Weather | T–2h | No | Coordinates of the **selected** origin station used for as-of weather. |
| `origin_airport_lat` / `origin_airport_lon` | double | Airports | Always | No | Airport centroid coordinates (from airport dim). |
| `dest_station_lat` / `dest_station_lon` | double | Weather | Pre-computed | No | Coordinates of nearest dest station (rank-1), for geography features only. |
| `dest_airport_lat` / `dest_airport_lon` | double | Airports | Always | No | Destination airport coordinates. |
| `origin_station_dis` | double (km) | Derived | T–2h | No | Haversine distance airport ↔ **chosen** origin station. Smaller is better. |
| `dest_station_dis` | double (km) | Derived | Pre-computed | No | Haversine distance destination airport ↔ rank-1 station. |
| `origin_type` | string | Airports (airport-codes CSV) | Always | No | Airport facility type for ORIGIN (e.g., `large_airport`, `medium_airport`, `small_airport`, `heliport`, `seaplane_base`). Useful categorical capturing operational complexity; one-hot or target-encode. |
| `dest_type` | string | Airports (airport-codes CSV) | Always | No | Airport facility type for DEST; same coding as `origin_type`. |


---

### Targets & Evaluation (keep; **never** feed to model)
| Feature | Type | Source | When available | Leakage? | Description / usage notes |
|---|---|---|---|---|---|
| `DEP_DEL15` | int (0/1) | Flights | After departure | **Yes** | Primary label: 1 if departure delay ≥ 15 min. Target only. |
| `DEP_DELAY` | double (min) | Flights | After departure | **Yes** | Continuous dep delay. Useful for calibration/cost curves. |
| `ARR_DEL15` | int (0/1) | Flights | After arrival | **Yes** | Optional secondary outcome for reports (not part of dep-delay model). |
| `ARR_DELAY` | double (min) | Flights | After arrival | **Yes** | Arrival delay; EDA only. |

---

### Post-Flight Diagnostics (EDA/debug; **never** feed to model)
| Feature | Type | Source | When available | Leakage? | Description / usage notes |
|---|---|---|---|---|---|
| `CARRIER_DELAY` | double (min) | Flights | Post-flight | **Yes** | Minutes attributed to carrier. Diagnostic only. |
| `WEATHER_DELAY` | double (min) | Flights | Post-flight | **Yes** | Minutes due to weather (BTS coding). |
| `NAS_DELAY` | double (min) | Flights | Post-flight | **Yes** | National Airspace System delay minutes. |
| `SECURITY_DELAY` | double (min) | Flights | Post-flight | **Yes** | Minutes due to security. |
| `LATE_AIRCRAFT_DELAY` | double (min) | Flights | Post-flight | **Yes** | Minutes due to late inbound aircraft. |
| `DEP_TIME` / `ARR_TIME` | int (HHMM) | Flights | Post-flight | **Yes** | Actual departure/arrival local time. |
| `TAXI_OUT` / `TAXI_IN` | int (min) | Flights | Post-flight | **Yes** | Actual taxi times. |
| `WHEELS_OFF` / `WHEELS_ON` | int (HHMM) | Flights | Post-flight | **Yes** | Actual off/on times. |
| `ACTUAL_ELAPSED_TIME` | int (min) | Flights | Post-flight | **Yes** | Actual duration. |
| `AIR_TIME` | int (min) | Flights | Post-flight | **Yes** | In-air time. |

---

### Curation Flags (keep until filtered)
| Feature | Type | Source | When available | Leakage? | Description / usage notes |
|---|---|---|---|---|---|
| `CANCELLED` | int (0/1) | Flights | Always | — | Filter to `0` for dep-delay modeling. |
| `CANCELLATION_CODE` | string | Flights | If cancelled | — | Reason (A=Carrier, B=Weather, C=NAS, D=Security). For analysis only. |
| `DIVERTED` | int (0/1) | Flights | After arrival | — | Filter to `0` for dep-delay modeling. |

---

### Practical Modeling Notes
- **Time handling:** Weather joins are UTC and **as-of** `prediction_utc` (no future look-ahead).  
- **Parsing weather:** Convert NOAA strings to numeric; add binary flags (e.g., precip>0, gust present).  
- **Cyclical times:** Derive `CRS_DEP_HOUR` and encode with sin/cos.  
- **High-cardinality:** `TAIL_NUM` and `OP_CARRIER_FL_NUM` can overfit; drop/hash/regularize.  
- **Collinearity:** `OP_UNIQUE_CARRIER` vs `OP_CARRIER` are often duplicates—keep one.  
- **Leakage guard:** Never include any “actual” time or delay field in training features.


## Load parquet file

In [0]:
# Read 1Y Joined dataset from raw files 
out_path = "dbfs:/student-groups/Group_4_4/JOINED_1Y_2019.parquet"
df_joined_1Y_2015 = spark.read.parquet(out_path)
print(f"Our Join row count: {df_joined_1Y_2015.count()}")

# Read 1Y Flights dataset from raw files
df_flights = spark.read.parquet(f"dbfs:/mnt/mids-w261/datasets_final_project_2022/parquet_airlines_data_1y/")
df_flights = df_flights.dropDuplicates()
print(f"Flights raw dataset row count: {df_flights.count()}")

# Load 1Y OTPW database
df_otpw = (
    spark.read
         .format("csv")
         .option("header", True)
         .option("inferSchema", True)
         .load("dbfs:/mnt/mids-w261/OTPW_12M/OTPW_12M/OTPW_12M_2015.csv.gz")
)
# df_otpw = spark.read.parquet(f"dbfs:/mnt/mids-w261/OTPW_60M/OTPW_60M/PartitionId=*/")
print(f"OTPW dataset row count: {df_otpw.count()}")

Our Join row count: 7422037
Flights raw dataset row count: 7422037


---------------------------------------------------------------------------
Py4JJavaError                             Traceback (most recent call last)
File <command-2411153393356460>, line 17
      9 print(f"Flights raw dataset row count: {df_flights.count()}")
     11 # Load 1Y OTPW database
     12 df_otpw = (
     13     spark.read
     14          .format("csv")
     15          .option("header", True)
     16          .option("inferSchema", True)
---> 17          .load("dbfs:/mnt/mids-w261/OTPW_12M/OTPW_12M/OTPW_12M_2015.csv.gz")
     18 )
     19 # df_otpw = spark.read.parquet(f"dbfs:/mnt/mids-w261/OTPW_60M/OTPW_60M/PartitionId=*/")
     20 print(f"OTPW dataset row count: {df_otpw.count()}")

File /databricks/spark/python/pyspark/instrumentation_utils.py:47, in _wrap_function.<locals>.wrapper(*args, **kwargs)
     45 start = time.perf_counter()
     46 try:
---> 47     res = func(*args, **kwargs)
     48     logger.log_success(
     49         module_name, class_name, function_n

In [0]:
from pyspark.sql import functions as F

# Read 1Y Joined dataset from raw files 
out_path = "dbfs:/student-groups/Group_4_4/JOINED_1Y_2019.parquet"
df_joined_1Y_2015 = spark.read.parquet(out_path)
print(f"Our Join row count: {df_joined_1Y_2015.count()}")

joined_dates = df_joined_1Y_2015.agg(
    F.min("FL_DATE").alias("min_FL_DATE"),
    F.max("FL_DATE").alias("max_FL_DATE")
).collect()[0]
print(f"JOINED_1Y_2015 FL_DATE range: {joined_dates['min_FL_DATE']} to {joined_dates['max_FL_DATE']}")

# Read 1Y Flights dataset from raw files
df_flights = spark.read.parquet("dbfs:/mnt/mids-w261/datasets_final_project_2022/parquet_airlines_data_1y/")
df_flights = df_flights.dropDuplicates()
print(f"Flights raw dataset row count: {df_flights.count()}")

flights_dates = df_flights.agg(
    F.min("FL_DATE").alias("min_FL_DATE"),
    F.max("FL_DATE").alias("max_FL_DATE")
).collect()[0]
print(f"Flights FL_DATE range: {flights_dates['min_FL_DATE']} to {flights_dates['max_FL_DATE']}")

# Load 1Y OTPW database
df_otpw = (
    spark.read
         .format("csv")
         .option("header", True)
         .option("inferSchema", True)
         .load("dbfs:/mnt/mids-w261/OTPW_12M/OTPW_12M/OTPW_12M_2015.csv.gz")
)
print(f"OTPW dataset row count: {df_otpw.count()}")

otpw_dates = df_otpw.agg(
    F.min("FL_DATE").alias("min_FL_DATE"),
    F.max("FL_DATE").alias("max_FL_DATE")
).collect()[0]
print(f"OTPW FL_DATE range: {otpw_dates['min_FL_DATE']} to {otpw_dates['max_FL_DATE']}")

Our Join row count: 7422037
JOINED_1Y_2015 FL_DATE range: 2019-01-01 to 2019-12-31
Flights raw dataset row count: 7422037
Flights FL_DATE range: 2019-01-01 to 2019-12-31
OTPW dataset row count: 5811854
OTPW FL_DATE range: 2015-01-01 to 2015-12-31


In [0]:
# --- Params ---
PATH_OTPW = "dbfs:/mnt/mids-w261/OTPW_12M/OTPW_12M/OTPW_12M_2015.csv.gz"  # adjust if you use 6m/1y/full
PATH_FINAL = "dbfs:/student-groups/Group_4_4/JOINED_1Y_2019.parquet"

OUT_IN   = "dbfs:/student-groups/Group_4_4/mart/final_curated_intersect_otpw"
OUT_NOT  = "dbfs:/student-groups/Group_4_4/mart/final_curated_not_in_otpw"

from pyspark.sql import functions as sf

# --- Load ---
otpw = (spark.read.option("header", True).option("inferSchema", True).csv(PATH_OTPW))
final_curated = spark.read.parquet(PATH_FINAL)

# --- Normalize OTPW columns to match our final_curated schema where needed ---
def norm_cols(df):
    rename = {}
    cols = set(df.columns)
    # Carrier
    if "CARRIER" in cols and "OP_UNIQUE_CARRIER" not in cols:
        rename["CARRIER"] = "OP_UNIQUE_CARRIER"
    if "OP_CARRIER" in cols and "OP_UNIQUE_CARRIER" not in cols:
        rename["OP_CARRIER"] = "OP_UNIQUE_CARRIER"
    # Flight number
    if "FL_NUM" in cols and "OP_CARRIER_FL_NUM" not in cols:
        rename["FL_NUM"] = "OP_CARRIER_FL_NUM"
    # CRS dep time
    if "CRS_DEP_TIME_LOCAL" in cols and "CRS_DEP_TIME" not in cols:
        rename["CRS_DEP_TIME_LOCAL"] = "CRS_DEP_TIME"
    return df.select([sf.col(c).alias(rename.get(c, c)) for c in df.columns])

otpw = norm_cols(otpw)

# --- Canonical key builders (strong uses time; weak omits time) ---
def with_key(df, use_time=True):
    base = (df
        .withColumn("FL_DATE_KEY", sf.to_date("FL_DATE"))
        .withColumn("CARRIER_KEY", sf.upper(sf.trim(sf.col("OP_UNIQUE_CARRIER"))))
        .withColumn("FLNUM_KEY",   sf.lpad(sf.col("OP_CARRIER_FL_NUM").cast("string"), 4, "0"))
        .withColumn("ORIGIN_KEY",  sf.upper(sf.trim(sf.col("ORIGIN"))))
        .withColumn("DEST_KEY",    sf.upper(sf.trim(sf.col("DEST"))))
    )
    if use_time:
        base = base.withColumn("CRS_DEP_KEY", sf.lpad(sf.col("CRS_DEP_TIME").cast("string"), 4, "0"))
        return base.withColumn("flight_key",
                sf.concat_ws("|","FL_DATE_KEY","CARRIER_KEY","FLNUM_KEY","ORIGIN_KEY","DEST_KEY","CRS_DEP_KEY"))
    else:
        return base.withColumn("flight_key",
                sf.concat_ws("|","FL_DATE_KEY","CARRIER_KEY","FLNUM_KEY","ORIGIN_KEY","DEST_KEY"))

# --- Build strong keys on both sides ---
otpw_strong = with_key(otpw, use_time=True).select("flight_key").distinct()
final_k_strong = with_key(final_curated, use_time=True)

# Optional: quick coverage check
total_fc = final_k_strong.count()
in_fc = final_k_strong.join(sf.broadcast(otpw_strong), "flight_key", "left_semi").count()
print(f"Strong-key coverage: {in_fc:,} / {total_fc:,} = {in_fc/total_fc:.2%}")

# If coverage seems unexpectedly low (schema/time mismatches), you can also try a weak key:
use_weak_key = False  # set to True if your strong-key coverage is too low and you accept looser matching
if use_weak_key:
    otpw_weak = with_key(otpw, use_time=False).select("flight_key").distinct().cache()
    final_k_weak = with_key(final_curated, use_time=False).cache()
    total_fc_w = final_k_weak.count()
    in_fc_w = final_k_weak.join(sf.broadcast(otpw_weak), "flight_key", "left_semi").count()
    print(f"Weak-key coverage: {in_fc_w:,} / {total_fc_w:,} = {in_fc_w/total_fc_w:.2%}")

# --- Produce EDA subsets using strong key (filter, not join) ---
otpw_keys = sf.broadcast(otpw_strong)

fc_in_otpw = final_k_strong.join(otpw_keys, on="flight_key", how="left_semi")
fc_not_in_otpw = final_k_strong.join(otpw_keys, on="flight_key", how="left_anti")

# Housekeeping: drop helper key parts if you prefer
drop_helpers = ["FL_DATE_KEY","CARRIER_KEY","FLNUM_KEY","ORIGIN_KEY","DEST_KEY","CRS_DEP_KEY"]
fc_in_otpw = fc_in_otpw.drop(*[c for c in drop_helpers if c in fc_in_otpw.columns])
fc_not_in_otpw = fc_not_in_otpw.drop(*[c for c in drop_helpers if c in fc_not_in_otpw.columns])

# --- Save for EDA ---
(fc_in_otpw.write.mode("overwrite").option("compression","snappy").parquet(OUT_IN))
(fc_not_in_otpw.write.mode("overwrite").option("compression","snappy").parquet(OUT_NOT))

print(f"✅ Wrote in-OTPW subset → {OUT_IN}")
print(f"✅ Wrote not-in-OTPW subset → {OUT_NOT}")


Strong-key coverage: 0 / 7,422,037 = 0.00%
✅ Wrote in-OTPW subset → dbfs:/student-groups/Group_4_4/mart/final_curated_intersect_otpw
✅ Wrote not-in-OTPW subset → dbfs:/student-groups/Group_4_4/mart/final_curated_not_in_otpw


In [0]:
display(df_joined_1Y_2015.orderBy(df_joined_1Y_2015.columns[0], ascending=True).limit(5))
display(df_joined_1Y_2015.orderBy(df_joined_1Y_2015.columns[0], ascending=False).limit(5))

flight_id prediction_utc origin_obs_utc asof_minutes origin_station_id dest_station_id FL_DATE YEAR QUARTER MONTH DAY_OF_MONTH DAY_OF_WEEK OP_UNIQUE_CARRIER OP_CARRIER OP_CARRIER_FL_NUM TAIL_NUM CRS_DEP_TIME CRS_ARR_TIME CRS_ELAPSED_TIME ORIGIN ORIGIN_AIRPORT_ID ORIGIN_CITY_NAME ORIGIN_STATE_ABR DEST DEST_AIRPORT_ID DEST_CITY_NAME DEST_STATE_ABR DISTANCE DISTANCE_GROUP HourlyDryBulbTemperature HourlyDewPointTemperature HourlyWetBulbTemperature HourlyPrecipitation HourlyWindSpeed HourlyWindDirection HourlyWindGustSpeed HourlyVisibility HourlyRelativeHumidity HourlyStationPressure HourlySeaLevelPressure HourlyAltimeterSetting HourlySkyConditions HourlyPresentWeatherType origin_station_lat origin_station_lon origin_airport_lat origin_airport_lon dest_station_lat dest_station_lon dest_airport_lat dest_airport_lon origin_station_dis dest_station_dis origin_type dest_type DEP_DEL15 DEP_DELAY ARR_DEL15 ARR_DELAY CARRIER_DELAY WEATHER_DELAY NAS_DELAY SECURITY_DELAY LATE_AIRCRAFT_DELAY DEP_TIME ARR_TIME TAXI_OUT TAXI_IN WHEELS_OFF WHEELS_ON ACTUAL_ELAPSED_TIME AIR_TIME CANCELLED CANCELLATION_CODE DIVERTED 2019-01-01|9E|3280|GNV|ATL 2019-01-01T09:00:00Z 2019-01-01T08:53:00Z 7 74756012816 72219013874 2019-01-01 2019 1 1 1 2 9E 9E 3280 N8688C 600 723 83.0 GNV 11953 Gainesville, FL FL ATL 10397 Atlanta, GA GA 300.0 2 64 64 64 0.00 0 000 null 7.00 100 30.04 30.22 30.22 SCT:04 55 null 29.692 -82.276 29.6865213 -82.27670959706018 33.63 -84.442 33.63779875 -84.42927118585675 0.6130486121159815 1.4631203352379507 medium_airport large_airport 0.0 1.0 0.0 -1.0 null null null null null 601 722 22.0 8.0 623 714 81.0 51.0 0.0 null 0.0 2019-01-01|9E|3281|MSP|CVG 2019-01-01T18:04:00Z 2019-01-01T18:00:00Z 4 72658014922 72421093814 2019-01-01 2019 1 1 1 2 9E 9E 3281 N348PQ 1404 1709 125.0 MSP 13487 Minneapolis, MN MN CVG 11193 Cincinnati, OH KY 596.0 3 7 -3 5 null 0 000 null 9.94 63 29.42 30.42 null null null 44.883 -93.229 44.878019050000006 -93.2209280537696 39.044 -84.672 39.0555 -84.66145 0.8433536890983956 1.5700857355975617 large_airport large_airport 0.0 -5.0 0.0 -36.0 null null null null null 1359 1633 15.0 4.0 1414 1629 94.0 75.0 0.0 null 0.0 2019-01-01|9E|3282|DTW|CVG 2019-01-01T15:20:00Z 2019-01-01T15:11:00Z 9 72537094847 72421093814 2019-01-01 2019 1 1 1 2 9E 9E 3282 N8896A 1220 1345 85.0 DTW 11433 Detroit, MI MI CVG 11193 Cincinnati, OH KY 229.0 1 32 28 30 T 8 030 null 1.50 85 29.50 null 30.22 BKN:07 10 OVC:08 15 -SN:03 |SN | 42.231 -83.331 42.205699100000004 -83.35297537621658 39.044 -84.672 39.0555 -84.66145 3.345110277884152 1.5700857355975617 large_airport large_airport 0.0 -5.0 0.0 -16.0 null null null null null 1215 1329 18.0 6.0 1233 1323 74.0 50.0 0.0 null 0.0 2019-01-01|9E|3283|TLH|ATL 2019-01-01T18:27:00Z 2019-01-01T17:53:00Z 34 72214093805 72219013874 2019-01-01 2019 1 1 1 2 9E 9E 3283 N8886A 1527 1639 72.0 TLH 15249 Tallahassee, FL FL ATL 10397 Atlanta, GA GA 223.0 1 72 68 69 0.00 8 140 null 10.00 87 30.06 30.14 30.14 FEW:02 15 OVC:08 250 null 30.393 -84.353 30.39782605 -84.35908394368526 33.63 -84.442 33.63779875 -84.42927118585675 0.7927627468378549 1.4631203352379507 medium_airport large_airport 0.0 -6.0 0.0 -14.0 null null null null null 1521 1625 14.0 7.0 1535 1618 64.0 43.0 0.0 null 0.0 2019-01-01|9E|3284|ATL|FSM 2019-01-01T22:02:00Z 2019-01-01T21:52:00Z 10 72219013874 72344013964 2019-01-01 2019 1 1 1 2 9E 9E 3284 N8974C 1902 2005 123.0 ATL 10397 Atlanta, GA GA FSM 11778 Fort Smith, AR AR 579.0 3 59 54 56 0.00 6 330 null 10.00 83 29.06 30.15 30.16 BKN:07 150 BKN:07 200 null 33.63 -84.442 33.63779875 -84.42927118585675 35.333 -94.363 35.3392525 -94.35697826263008 1.4631203352379507 0.8841592542977278 large_airport medium_airport 0.0 -15.0 0.0 -25.0 null null null null null 1847 1940 18.0 5.0 1905 1935 113.0 90.0 0.0 null 0.0

flight_id prediction_utc origin_obs_utc asof_minutes origin_station_id dest_station_id FL_DATE YEAR QUARTER MONTH DAY_OF_MONTH DAY_OF_WEEK OP_UNIQUE_CARRIER OP_CARRIER OP_CARRIER_FL_NUM TAIL_NUM CRS_DEP_TIME CRS_ARR_TIME CRS_ELAPSED_TIME ORIGIN ORIGIN_AIRPORT_ID ORIGIN_CITY_NAME ORIGIN_STATE_ABR DEST DEST_AIRPORT_ID DEST_CITY_NAME DEST_STATE_ABR DISTANCE DISTANCE_GROUP HourlyDryBulbTemperature HourlyDewPointTemperature HourlyWetBulbTemperature HourlyPrecipitation HourlyWindSpeed HourlyWindDirection HourlyWindGustSpeed HourlyVisibility HourlyRelativeHumidity HourlyStationPressure HourlySeaLevelPressure HourlyAltimeterSetting HourlySkyConditions HourlyPresentWeatherType origin_station_lat origin_station_lon origin_airport_lat origin_airport_lon dest_station_lat dest_station_lon dest_airport_lat dest_airport_lon origin_station_dis dest_station_dis origin_type dest_type DEP_DEL15 DEP_DELAY ARR_DEL15 ARR_DELAY CARRIER_DELAY WEATHER_DELAY NAS_DELAY SECURITY_DELAY LATE_AIRCRAFT_DELAY DEP_TIME ARR_TIME TAXI_OUT TAXI_IN WHEELS_OFF WHEELS_ON ACTUAL_ELAPSED_TIME AIR_TIME CANCELLED CANCELLATION_CODE DIVERTED 2019-12-31|YX|6140|ROC|LGA 2019-12-31T10:00:00Z 2019-12-31T09:54:00Z 6 72529014768 72503014732 2019-12-31 2019 4 12 31 2 YX YX 6140 N244JQ 700 832 92.0 ROC 14576 Rochester, NY NY LGA 12953 New York, NY NY 254.0 2 38 31 35 0.00 9 210 null 10.00 76 28.99 29.60 29.58 FEW:02 35 BKN:07 60 OVC:08 200 null 43.117 -77.677 43.12759065 -77.66522075259782 40.779 -73.88 40.7757145 -73.87336398511545 1.5168292888850612 0.6676019544429856 medium_airport large_airport 0.0 -7.0 0.0 -28.0 null null null null null 653 804 11.0 7.0 704 757 71.0 53.0 0.0 null 0.0 2019-12-31|YX|6139|ORD|BOS 2019-12-31T15:57:00Z 2019-12-31T15:51:00Z 6 72530094846 72509014739 2019-12-31 2019 4 12 31 2 YX YX 6139 N860RW 1157 1523 146.0 ORD 13930 Chicago, IL IL BOS 10721 Boston, MA MA 867.0 4 26 19 24 0.00 17 260 23 10.00 75 29.05 29.80 29.77 OVC:08 23 null 41.995 -87.934 41.97795725 -87.90917584851792 42.361 -71.01 42.3629737 -71.01350667543224 2.7930256931701187 0.362182815141868 large_airport large_airport 1.0 32.0 1.0 22.0 22.0 0.0 0.0 0.0 0.0 1229 1545 23.0 6.0 1252 1539 136.0 107.0 0.0 null 0.0 2019-12-31|YX|6139|BOS|ORD 2019-12-31T12:20:00Z 2019-12-31T11:54:00Z 26 72509014739 72530094846 2019-12-31 2019 4 12 31 2 YX YX 6139 N240JQ 920 1127 187.0 BOS 10721 Boston, MA MA ORD 13930 Chicago, IL IL 867.0 4 39 35 37 0.00 10 330 null 7.00 86 29.52 29.55 29.55 OVC:08 6 null 42.361 -71.01 42.3629737 -71.01350667543224 41.995 -87.934 41.97795725 -87.90917584851792 0.362182815141868 2.7930256931701187 large_airport large_airport 0.0 -2.0 0.0 -3.0 null null null null null 918 1124 26.0 29.0 944 1055 186.0 131.0 0.0 null 0.0 2019-12-31|YX|6133|BOS|ORD 2019-12-31T20:45:00Z 2019-12-31T19:54:00Z 51 72509014739 72530094846 2019-12-31 2019 4 12 31 2 YX YX 6133 N204JQ 1745 1956 191.0 BOS 10721 Boston, MA MA ORD 13930 Chicago, IL IL 867.0 4 39 33 37 0.00 8 260 null 10.00 79 29.53 29.56 29.56 FEW:02 8 BKN:07 10 OVC:08 65 null 42.361 -71.01 42.3629737 -71.01350667543224 41.995 -87.934 41.97795725 -87.90917584851792 0.362182815141868 2.7930256931701187 large_airport large_airport 0.0 -8.0 0.0 -39.0 null null null null null 1737 1917 16.0 10.0 1753 1907 160.0 134.0 0.0 null 0.0 2019-12-31|YX|6131|LGA|BUF 2019-12-31T20:00:00Z 2019-12-31T19:51:00Z 9 72503014732 72528014733 2019-12-31 2019 4 12 31 2 YX YX 6131 N203JQ 1700 1837 97.0 LGA 12953 New York, NY NY BUF 10792 Buffalo, NY NY 292.0 2 45 35 41 0.00 10 210 null 10.00 68 29.59 29.62 29.62 BKN:07 50 OVC:08 60 null 40.779 -73.88 40.7757145 -73.87336398511545 42.941 -78.736 42.9402016 -78.73075229745353 0.6676019544429856 0.4362986842122279 large_airport large_airport 0.0 -12.0 0.0 -36.0 null null null null null 1648 1801 12.0 6.0 1700 1755 73.0 55.0 0.0 null 0.0

In [0]:
df_ppg_flights = df_joined_1Y_2015.filter((df_joined_1Y_2015.ORIGIN == "PPG") | (df_joined_1Y_2015.DEST == "PPG"))
display(df_ppg_flights)

flight_id prediction_utc origin_obs_utc asof_minutes origin_station_id dest_station_id FL_DATE YEAR QUARTER MONTH DAY_OF_MONTH DAY_OF_WEEK OP_UNIQUE_CARRIER OP_CARRIER OP_CARRIER_FL_NUM TAIL_NUM CRS_DEP_TIME CRS_ARR_TIME CRS_ELAPSED_TIME ORIGIN ORIGIN_AIRPORT_ID ORIGIN_CITY_NAME ORIGIN_STATE_ABR DEST DEST_AIRPORT_ID DEST_CITY_NAME DEST_STATE_ABR DISTANCE DISTANCE_GROUP HourlyDryBulbTemperature HourlyDewPointTemperature HourlyWetBulbTemperature HourlyPrecipitation HourlyWindSpeed HourlyWindDirection HourlyWindGustSpeed HourlyVisibility HourlyRelativeHumidity HourlyStationPressure HourlySeaLevelPressure HourlyAltimeterSetting HourlySkyConditions HourlyPresentWeatherType origin_station_lat origin_station_lon origin_airport_lat origin_airport_lon dest_station_lat dest_station_lon dest_airport_lat dest_airport_lon origin_station_dis dest_station_dis origin_type dest_type DEP_DEL15 DEP_DELAY ARR_DEL15 ARR_DELAY CARRIER_DELAY WEATHER_DELAY NAS_DELAY SECURITY_DELAY LATE_AIRCRAFT_DELAY DEP_TIME ARR_TIME TAXI_OUT TAXI_IN WHEELS_OFF WHEELS_ON ACTUAL_ELAPSED_TIME AIR_TIME CANCELLED CANCELLATION_CODE DIVERTED 2019-01-10|HA|466|PPG|HNL 2019-01-11T08:20:00Z 2019-01-11T07:53:00Z 27 91197521510 91182022521 2019-01-10 2019 1 1 10 4 HA HA 466 N388HA 2320 550 330.0 PPG 14222 Pago Pago, TT TT HNL 12173 Honolulu, HI HI 2599.0 11 71 60 64 0.00 3 100 null 10.00 68 29.99 30.04 30.04 SCT:04 55 null 19.736 -156.049 -14.3347658 -170.71596862723766 21.324 -157.929 21.32040435 -157.9173135198164 4114.283979810308 1.2748484015654673 medium_airport large_airport 0.0 13.0 0.0 6.0 null null null null null 2333 556 14.0 6.0 2347 550 323.0 303.0 0.0 null 0.0 2019-01-31|HA|466|PPG|HNL 2019-02-01T08:20:00Z 2019-02-01T07:53:00Z 27 91197521510 91182022521 2019-01-31 2019 1 1 31 4 HA HA 466 N381HA 2320 550 330.0 PPG 14222 Pago Pago, TT TT HNL 12173 Honolulu, HI HI 2599.0 11 71 65 67 0.00 8 130 null 10.00 81 29.84 29.89 29.89 FEW:02 35 null 19.736 -156.049 -14.3347658 -170.71596862723766 21.324 -157.929 21.32040435 -157.9173135198164 4114.283979810308 1.2748484015654673 medium_airport large_airport 0.0 12.0 0.0 5.0 null null null null null 2332 555 14.0 10.0 2346 545 323.0 299.0 0.0 null 0.0 2019-02-07|HA|466|PPG|HNL 2019-02-08T08:25:00Z 2019-02-08T07:53:00Z 32 91197521510 91182022521 2019-02-07 2019 1 2 7 4 HA HA 466 N370HA 2325 550 325.0 PPG 14222 Pago Pago, TT TT HNL 12173 Honolulu, HI HI 2599.0 11 71 63 66 0.00 6 050 null 10.00 76 29.88 29.93 29.93 FEW:02 35 null 19.736 -156.049 -14.3347658 -170.71596862723766 21.324 -157.929 21.32040435 -157.9173135198164 4114.283979810308 1.2748484015654673 medium_airport large_airport 0.0 1.0 0.0 6.0 null null null null null 2326 556 25.0 8.0 2351 548 330.0 297.0 0.0 null 0.0 2019-06-11|HA|466|PPG|HNL 2019-06-12T08:20:00Z 2019-06-12T07:53:00Z 27 91197521510 91182022521 2019-06-11 2019 2 6 11 2 HA HA 466 N379HA 2320 550 330.0 PPG 14222 Pago Pago, TT TT HNL 12173 Honolulu, HI HI 2599.0 11 82 59 68 0.00 11 010 null 10.00 46 29.96 30.01s 30.01 FEW:02 50 null 19.736 -156.049 -14.3347658 -170.71596862723766 21.324 -157.929 21.32040435 -157.9173135198164 4114.283979810308 1.2748484015654673 medium_airport large_airport 0.0 -5.0 0.0 0.0 null null null null null 2315 550 18.0 7.0 2333 543 335.0 310.0 0.0 null 0.0 2019-06-25|HA|466|PPG|HNL 2019-06-26T08:20:00Z 2019-06-26T07:53:00Z 27 91197521510 91182022521 2019-06-25 2019 2 6 25 2 HA HA 466 N385HA 2320 550 330.0 PPG 14222 Pago Pago, TT TT HNL 12173 Honolulu, HI HI 2599.0 11 81 69 73 0.00 13 020 null 10.00 67 29.83 29.87s 29.87 SCT:04 55 SCT:04 70 null 19.736 -156.049 -14.3347658 -170.71596862723766 21.324 -157.929 21.32040435 -157.9173135198164 4114.283979810308 1.2748484015654673 medium_airport large_airport 1.0 50.0 1.0 48.0 0.0 0.0 0.0 0.0 48.0 10 638 18.0 9.0 28 629 328.0 301.0 0.0 null 0.0 2019-09-12|HA|466|PPG|HNL 2019-09-13T08:20:00Z 2019-09-13T07:53:00Z 27 91197521510 91182022521 2019-09-12 2019 3 9 12 4 HA HA 466 N395HA 2320 550 330.0 PPG 14222 Pago Pago, TT TT HNL 12173 Honolu

In [0]:
df_weather = spark.read.parquet(f"dbfs:/mnt/mids-w261/datasets_final_project_2022/parquet_weather_data_1y/")

In [0]:
df_weather_91182022521 = df_weather.filter(df_weather.STATION == "91182022521")
display(df_weather_91182022521)

STATION DATE LATITUDE LONGITUDE ELEVATION NAME REPORT_TYPE SOURCE HourlyAltimeterSetting HourlyDewPointTemperature HourlyDryBulbTemperature HourlyPrecipitation HourlyPresentWeatherType HourlyPressureChange HourlyPressureTendency HourlyRelativeHumidity HourlySkyConditions HourlySeaLevelPressure HourlyStationPressure HourlyVisibility HourlyWetBulbTemperature HourlyWindDirection HourlyWindGustSpeed HourlyWindSpeed Sunrise Sunset DailyAverageDewPointTemperature DailyAverageDryBulbTemperature DailyAverageRelativeHumidity DailyAverageSeaLevelPressure DailyAverageStationPressure DailyAverageWetBulbTemperature DailyAverageWindSpeed DailyCoolingDegreeDays DailyDepartureFromNormalAverageTemperature DailyHeatingDegreeDays DailyMaximumDryBulbTemperature DailyMinimumDryBulbTemperature DailyPeakWindDirection DailyPeakWindSpeed DailyPrecipitation DailySnowDepth DailySnowfall DailySustainedWindDirection DailySustainedWindSpeed DailyWeather MonthlyAverageRH MonthlyDaysWithGT001Precip MonthlyDaysWithGT010Precip MonthlyDaysWithGT32Temp MonthlyDaysWithGT90Temp MonthlyDaysWithLT0Temp MonthlyDaysWithLT32Temp MonthlyDepartureFromNormalAverageTemperature MonthlyDepartureFromNormalCoolingDegreeDays MonthlyDepartureFromNormalHeatingDegreeDays MonthlyDepartureFromNormalMaximumTemperature MonthlyDepartureFromNormalMinimumTemperature MonthlyDepartureFromNormalPrecipitation MonthlyDewpointTemperature MonthlyGreatestPrecip MonthlyGreatestPrecipDate MonthlyGreatestSnowDepth MonthlyGreatestSnowDepthDate MonthlyGreatestSnowfall MonthlyGreatestSnowfallDate MonthlyMaxSeaLevelPressureValue MonthlyMaxSeaLevelPressureValueDate MonthlyMaxSeaLevelPressureValueTime MonthlyMaximumTemperature MonthlyMeanTemperature MonthlyMinSeaLevelPressureValue MonthlyMinSeaLevelPressureValueDate MonthlyMinSeaLevelPressureValueTime MonthlyMinimumTemperature MonthlySeaLevelPressure MonthlyStationPressure MonthlyTotalLiquidPrecipitation MonthlyTotalSnowfall MonthlyWetBulb AWND CDSD CLDD DSNW HDSD HTDD NormalsCoolingDegreeDay NormalsHeatingDegreeDay ShortDurationEndDate005 ShortDurationEndDate010 ShortDurationEndDate015 ShortDurationEndDate020 ShortDurationEndDate030 ShortDurationEndDate045 ShortDurationEndDate060 ShortDurationEndDate080 ShortDurationEndDate100 ShortDurationEndDate120 ShortDurationEndDate150 ShortDurationEndDate180 ShortDurationPrecipitationValue005 ShortDurationPrecipitationValue010 ShortDurationPrecipitationValue015 ShortDurationPrecipitationValue020 ShortDurationPrecipitationValue030 ShortDurationPrecipitationValue045 ShortDurationPrecipitationValue060 ShortDurationPrecipitationValue080 ShortDurationPrecipitationValue100 ShortDurationPrecipitationValue120 ShortDurationPrecipitationValue150 ShortDurationPrecipitationValue180 REM BackupDirection BackupDistance BackupDistanceUnit BackupElements BackupElevation BackupEquipment BackupLatitude BackupLongitude BackupName WindEquipmentChangeDate YEAR 91182022521 2019-01-01T00:53:00 21.324 -157.9294 2.1 HONOLULU INTERNATIONAL AIRPORT, HI US FM-15 7 30.02 64 77 0.00 null null null 64 FEW:02 25 FEW:02 45 30.02 30.00 10.00 69 050 null 14 null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null MET10001/01/19 00:53:02 METAR PHNL 011053Z 05012KT 10SM FEW025 FEW045 25/18 A3002 RMK AO2 SLP165 T02500178 SE 0.86 mi PRECIP 10 SRG 21.3219 -157.9253 CONTRACTOR 2009-05-12 2019 91182022521 2019-01-01T01:53:00 21.324 -157.9294 2.1 HONOLULU INTERNATIONAL AIRPORT, HI US FM-15 7 30.02 66 77 T null +0.01 5 69 FEW:02 22 FEW:02 39 SCT:04 49 30.02 30.00 10.00 70 060 null 11 null null null null null null null null null null null null null null null null null null null null 